# DataDiVR | DISEASE ANNOTATIONS

In [5]:
from multidimvis_main import *

In [6]:
G = nx.read_edgelist('input/ppi_elist.txt',data=False)

d_gene_do = pickle.load( open( "input/d_gene_do.pkl", "rb" ) )
d_do_genes = pickle.load( open( "input/d_do_genes.pkl", "rb" ) )
d_do_names = pickle.load( open( "input/DO_names.pkl", "rb" ) )
d_names_do = {y:x for x,y in d_do_names.items()}

In [7]:
# precalculated import
df_centralities = pd.read_csv('output_csv/Features_centralities_Dataframe_Human.csv', index_col=0)

d_deghubs = dict(zip(G.nodes(),df_centralities['degs']))
d_clos = dict(zip(G.nodes(), df_centralities['clos']))
d_betw = dict(zip(G.nodes(), df_centralities['betw']))
d_eigen = dict(zip(G.nodes(), df_centralities['eigen']))

### GENE ID to SYN (e.g. HOVERINFO for nodes)

In [8]:
entrez_syn = pd.read_csv('input/entrezid_syn.csv', index_col=0)
d_entrez_syn = dict(zip(entrez_syn.index,entrez_syn['db_synonym']))

d_gene2syn = {}
for k,v in d_entrez_syn.items():
    try:
        if k in G.nodes():
            d_gene2syn[k] = v
    except: 
           d_gene2syn['None'] = 'no entry'
            
d_genes_withsyn = {}
for g in G.nodes():
    for k,v in d_gene2syn.items():
        if g == k:
            d_genes_withsyn[g] = v
            
d_genes_nosyn = {}
for gene in G.nodes():
    if gene not in d_genes_withsyn.keys():
        d_genes_nosyn[gene] = 'no entry'
        
d_genes_all = {**d_genes_withsyn, **d_genes_nosyn}
d_genes_syn_sorted = {key:d_genes_all[key] for key in G.nodes()}

l_genes_syn=[]
for k,v in d_genes_syn_sorted.items():
    try:
        l_genes_syn.append(set(v.split('|')))
    except:
        l_genes_syn.append(v)
        
d_genes_syn_complete = {}
for i,v in enumerate(d_genes_syn_sorted.keys()):
    for idx,l in enumerate(l_genes_syn):
        if i==idx:
            d_genes_syn_complete[v] = l
            
l_features = list(zip(d_genes_syn_complete.keys(),d_genes_syn_complete.values()))

## Gene to Disease associated 

In [175]:
f_dis = pd.read_csv('input/felix/ppi_layout_4_disease.csv',index_col=0, header=None, names = ['X','Y','Z','r','g','b'])

In [174]:
d_doid_genes = pickle.load(open("input/celine/d_doid2ent_incUpstream5to100_s20200707.pkl", "rb"))

In [176]:
# get precalculated COORDINATES (FELIX LAYOUT > DATADiVR) 
f_DIS_genes = []
for i in list(f_dis.index):
    f_DIS_genes.append(str(i))
    
f_DIS_x = f_dis['X']
f_DIS_y = f_dis['Y']
f_DIS_z = f_dis['Z']

posG_DIS = dict(zip(f_DIS_genes,zip(f_DIS_x,f_DIS_y, f_DIS_z)))
posG_DIS_sorted = {key: posG_DIS[key] for key in G.nodes()}

posG = posG_DIS_sorted

### IBD Genes

In [44]:
IBD_genes = np.loadtxt("input/iei_hubness.txt", usecols=(0, 1), skiprows=1, dtype=str)

d_IBD_genes = {}
for i in IBD_genes:
    d_IBD_genes[i[0]] = i[1]
    
d_degs = dict(G.degree())
d_degs_sortbydegree = {k: v for k, v in sorted(d_degs.items(), key=lambda item: item[1], reverse=True)}

# dict with gene to syn
d_geneid_IBDsyn = {}
for g in d_IBD_genes.keys():
    for k,v in d_genes_syn_complete.items():
        try:
            for gene in v:
                if g == gene:
                    d_geneid_IBDsyn[k] = g
        except:
            pass
    
# dict with gene to syn
d_IBDsyn_geneid = {}
for g in d_IBD_genes.keys():
    for k,v in d_genes_syn_complete.items():
        try:
            for gene in v:
                if g == gene:
                    d_IBDsyn_geneid[g] = k
        except:
            pass
        

# DISEASE Association with IBD genes 

d_IBD_doids = {}
for g,doids in d_gene_do.items():
    for idx,syn in d_geneid_IBDsyn.items():
        if g == idx: 
            d_IBD_doids[syn] = doids

____________
# PRE-SETTINGS
____________

### NODE SIZE

In [144]:
size3d = 2

scalef= 0.01
#size3d = draw_node_degree(G, scalef)

### COLOUR PARAMETERS + 3D ANNOTATIONS
choose one of the following: 

+ FELIX COLOURS

In [149]:
f_DIS_r = f_dis['r'] 
f_DIS_g = f_dis['g']
f_DIS_b = f_dis['b']

f_colours = dict(zip(f_DIS_genes, list(zip(f_DIS_r, f_DIS_g, f_DIS_b))))

In [157]:
f_colours_sorted = {key:f_colours[key] for key in G.nodes()}

colours = list(f_colours_sorted.values())

#### ONE GENE

In [140]:
feature = 'IBD-NFKB1'

# set list of genes with same color: 
l_genes = [list(d_IBDsyn_geneid.values())[0]]

colours = color_nodes_from_genelist(G, l_genes, 'red')

# Annotation of one specific IBD Gene (NFKB1)

d_genes_coords = {}
for node,val in d_geneid_IBDsyn.items():
    for k,v in posG.items():
        if node == str(k):
            d_genes_coords[node] = v
            
g_x = []
g_y = []
g_z = []
for node,coords in d_genes_coords.items():
    g_x.append(coords[0])
    g_y.append(coords[1])
    g_z.append(coords[2])

# Choose Specific Gene to annotate 
geneid = '4790'
genesyn = d_geneid_IBDsyn['4790'] 

x_gene = posG[geneid][0]
y_gene = posG[geneid][1]
z_gene = posG[geneid][2]

annotations = [dict ( 
                x=x_gene,
                y=y_gene,            
                z=z_gene, 
                showarrow=True,
                text = 'IBD GENE: '+genesyn,
                ay = -100,
                ax = -100,
                opacity = 0.8,
                arrowhead = 0,
                arrowwidth = 0.5 ,
                arrowcolor = "white" 
            )]

#### DISEASE CATEGORY

In [224]:
# ----------------------------------------------------        
# get disease categories
# ----------------------------------------------------        
disease_categories = {}
for d_name in d_names_do.keys():
    #if d_name.find(disease_category) != -1:
        try:
            disease_categories[d_name,d_names_do[d_name]]=len(d_do_genes[d_names_do[d_name]])
            #print('specific disease: %s (%s) ; # associated genes: %s' %(d_name,d_names_do[d_name],len(d_do_genes[d_names_do[d_name]])))
        except:
            pass

# ----------------------------------------------------        
# search specific term + count of genes associated with disease 
# ----------------------------------------------------   
min_diseasegenes = 0
max_diseasegenes = 5000
search_term = 'bowel'

for k,v in disease_categories.items():
    if v >= min_diseasegenes and v<= max_diseasegenes and search_term in k[0]:
        print(k,v)

('inflammatory bowel disease', 'DOID:0050589') 128
('irritable bowel syndrome', 'DOID:9778') 2
('bowel dysfunction', 'DOID:9779') 136


In [229]:
disease_category = 'inflammatory bowel disease'
disease_col = 'red'

feature = disease_category

l_genes = get_disease_genes(G, d_names_do, d_do_genes, disease_category)
#colours = color_diseasecategory(G, d_names_do, d_do_genes, disease_category, disease_col)
colours = color_nodes_from_genelist(G, l_genes, disease_col)

annotations = [dict(
                x=max(posG.values())[0],
                y=max(posG.values())[1],
                z=max(posG.values())[2],
                showarrow=True,
                text=disease_category,
                xanchor="right",
                ay=-100,
                ax=-100,
                opacity=0.8,
                arrowhead=0,
                arrowwidth=0.5,
                arrowcolor="white"
                )]

print('Genes associated with Disease "'+disease_category+'" : ', len(l_genes))

Genes associated with Disease "inflammatory bowel disease" :  128


#### COLOR EDGES BASED ON GENE LIST

In [230]:
d_edge_col = color_edges_from_specnodes(G, l_genes, disease_col)
edge_color = list(d_edge_col.values())

____
## PORTRAITS
____

In [231]:
tsne_edges = get_trace_spec_edges_only(list(d_edge_col.keys()), posG, disease_col)
tsne_nodes = get_trace_nodes_(posG, l_features, colours, size3d)

tsne_data = [tsne_edges, tsne_nodes]
#tsne_data = [tsne_nodes, trace_centers]
#tsne_data = [tsne_nodes]

In [232]:
fig = pgo.Figure()
for i in tsne_data:
    fig.add_trace(i)
fig.update_layout(template='plotly_dark', showlegend=False, width=1200, height=1200,
                  scene=dict(
                    aspectratio=dict(
                        x=1,
                        y=1,
                        z=1
                    ),
                    camera=dict(
                        center=dict(
                            x=0,
                            y=0,
                            z=0
                        ),
                        eye=dict(
                            x=1.96903462608,
                            y=-1.09022831971,
                            z=0.405345349304
                        ),
                        up=dict(
                            x=0,
                            y=0,
                            z=1
                        )
                    ),
                    dragmode="turntable",
                    annotations=annotations,
                ))
py.iplot(fig)

plotly.offline.plot(fig, filename = 'output_plots/3Dportrait_DISlayout_'+feature+'_Human.html', auto_open=False)

'output_plots/3Dportrait_DISlayout_inflammatory bowel disease_Human.html'